In [6]:
%matplotlib inline
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import itertools
import pickle as pk
from scipy.stats import binom
from scipy.stats import poisson
from scipy.stats import expon
from scipy import stats

In [27]:
def get_KL(v1, v2, is_P=0):
    if is_P == 0:
        v1 = np.array(v1)
        v2 = np.array(v2)
        p_v1 = v1 / sum(v1)
        p_v2 = v2 / sum(v2)
    else:
        p_v1 = v1
        p_v2 = v2
    KL = 0
    for i in range(len(v1)):
        if p_v1[i] > 0 and p_v2[i] > 0:
            KL += p_v1[i] * np.log2(p_v1[i] / p_v2[i])
    return KL


def get_JS(v1, v2, w1=0.5, w2=0.5):
    v1 = np.array(v1)
    v2 = np.array(v2)

    p_v1 = v1 / sum(v1)
    p_v2 = v2 / sum(v2)
    p_avg = (p_v1 + p_v2) / 2
    JS = w1 * get_KL(p_v1, p_avg, 1) + w2 * get_KL(p_v2, p_avg, 1)
    return JS

In [23]:
## Luna
df = pd.read_excel('data/HNa_Luna.xlsx')
df

mz         inten  charge  H  Na          com  num  limit
0    575.96602  9.285062e+07       2  2   0  dA[1,2,0,6]    1      8
1    586.95628  1.062081e+08       2  3   1  dA[1,2,0,6]    1      8
2    597.94706  6.898725e+07       2  4   2  dA[1,2,0,6]    1      8
3    608.93831  4.418838e+07       2  5   3  dA[1,2,0,6]    1      8
4    619.92924  2.997720e+07       2  6   4  dA[1,2,0,6]    1      8
..         ...           ...     ... ..  ..          ...  ...    ...
157  529.98813  2.752349e+07       3  4   1  dA[2,3,0,7]   24     10
158  537.31555  6.501848e+06       3  5   2  dA[2,3,0,7]   24     10
159  544.64363  3.735246e+06       3  6   3  dA[2,3,0,7]   24     10
160  551.96815  8.622922e+05       3  7   4  dA[2,3,0,7]   24     10
161  566.95408  2.842080e+05       3  9   6  dA[2,3,0,7]   24     10

[162 rows x 8 columns]

In [28]:
 df['weight'] = df['inten']*df['Na']
 df

mz         inten  charge  H  Na          com  num  limit  \
0    575.96602  9.285062e+07       2  2   0  dA[1,2,0,6]    1      8   
1    586.95628  1.062081e+08       2  3   1  dA[1,2,0,6]    1      8   
2    597.94706  6.898725e+07       2  4   2  dA[1,2,0,6]    1      8   
3    608.93831  4.418838e+07       2  5   3  dA[1,2,0,6]    1      8   
4    619.92924  2.997720e+07       2  6   4  dA[1,2,0,6]    1      8   
..         ...           ...     ... ..  ..          ...  ...    ...   
157  529.98813  2.752349e+07       3  4   1  dA[2,3,0,7]   24     10   
158  537.31555  6.501848e+06       3  5   2  dA[2,3,0,7]   24     10   
159  544.64363  3.735246e+06       3  6   3  dA[2,3,0,7]   24     10   
160  551.96815  8.622922e+05       3  7   4  dA[2,3,0,7]   24     10   
161  566.95408  2.842080e+05       3  9   6  dA[2,3,0,7]   24     10   

           weight  
0    0.000000e+00  
1    1.062081e+08  
2    1.379745e+08  
3    1.325651e+08  
4    1.199088e+08  
..            ...  
157  2.752349e+07  
158  1.300370e+07  
159  1.120574e+07  
160  3.449169e+06  
161  1.705248e+06  

[162 rows x 9 columns]

In [29]:
group = df.num.unique()
group

array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24])

In [85]:
fig, axs = plt.subplots(6,4,figsize=(30, 30),dpi=300)
for n in group:
    tmp_df = df[df['num']==n]
    tmp_df.index = range(tmp_df.shape[0])
    lambd = sum(tmp_df['weight'])/sum(tmp_df['inten'])
    x = np.array(tmp_df['Na'])
    lim = tmp_df.loc[0,'limit']
    com = tmp_df.loc[0,'com']
    y_real = []
    y_the = []
    for i in tmp_df.index:
        tmp_x = tmp_df.loc[i,'Na']
        tmp_real = tmp_df.loc[i,'inten']
        tmp_the = poisson.pmf(tmp_x,lambd)
        y_real.append(tmp_real)
        y_the.append(tmp_the)
    y_real =np.array(y_real)/y_real[0]*100
    y_the = np.array(y_the)/y_the[0]*100
    tmp_JS = np.round(get_JS(y_real,y_the),5)
    tmp_per = np.round(stats.pearsonr(y_real,y_the),5)
    # plt.figure(figsize=(8,6),dpi=300)
    lw1 = 2
    lw2 = 1
    a1 = (n-1)//4
    a2 = (n-1)%4
    for i in range(len(x)):
        xx = x[i]
        y1 = y_real[i]
        y2 = y_the[i]
        axs[a1,a2].plot([xx,xx],[0,y1], lw=lw1, c='grey', zorder=1)
        axs[a1,a2].plot([xx,xx],[0,-y2], lw=lw2, c='b', zorder=2)
    sns.despine()
    axs[a1,a2].plot([min(x)-1,max(x)+1],[0,0],lw =2, c = 'k')
    axs[a1,a2].plot([0,0],[0,0],lw=lw1, c='grey',label='Exp_sp')
    axs[a1,a2].plot([0,0],[0,0],lw=lw2, c='b',label='The_sp')
    axs[a1,a2].set_title(str(com)+', JS='+str(tmp_per)+', lambda='+str(np.round(lambd,5)))
    axs[a1,a2].legend(frameon =False)
plt.tight_layout(pad=2) 
plt.show()


In [ ]:
a1

In [86]:
fig, axs = plt.subplots(6,4,figsize=(30, 30),dpi=300)
for n in group:
    tmp_df = df[df['num']==n]
    tmp_df.index = range(tmp_df.shape[0])
    lambd = sum(tmp_df['weight'])/sum(tmp_df['inten'])
    # print(lambd)
    x = np.array(tmp_df['Na'])
    lim = tmp_df.loc[0,'limit']
    com = tmp_df.loc[0,'com']
    y_real = []
    y_the = []
    for i in tmp_df.index:
        tmp_x = tmp_df.loc[i,'Na']
        tmp_real = tmp_df.loc[i,'inten']
        tmp_the = expon.pdf(tmp_x,loc=min(x),scale=lambd)
        y_real.append(tmp_real)
        y_the.append(tmp_the)
    y_real =np.array(y_real)/y_real[0]*100
    y_the = np.array(y_the)/y_the[0]*100
    tmp_JS = np.round(get_JS(y_real,y_the),5)
    tmp_per = np.round(stats.pearsonr(y_real,y_the),5)
    # plt.figure(figsize=(8,6),dpi=300)
    lw1 = 2
    lw2 = 1
    a1 = (n-1)//4
    a2 = (n-1)%4
    for i in range(len(x)):
        xx = x[i]
        y1 = y_real[i]
        y2 = y_the[i]
        axs[a1,a2].plot([xx,xx],[0,y1], lw=lw1, c='grey', zorder=1)
        axs[a1,a2].plot([xx,xx],[0,-y2], lw=lw2, c='b', zorder=2)
    sns.despine()
    axs[a1,a2].plot([min(x)-1,max(x)+1],[0,0],lw =2, c = 'k')
    axs[a1,a2].plot([0,0],[0,0],lw=lw1, c='grey',label='Exp_sp')
    axs[a1,a2].plot([0,0],[0,0],lw=lw2, c='b',label='The_sp')
    axs[a1,a2].set_title(str(com)+', JS='+str(tmp_per)+', lambda='+str(np.round(lambd,5)))
    axs[a1,a2].legend(frameon =False)
plt.tight_layout(pad=2) 
plt.show()

In [47]:
expon.pdf(0.01,scale=1/2)

1.9603973466135105

In [55]:
tmpi

array([0.00000000e+00, 8.17775726e-05, 3.84521484e-03, 3.04162502e-02,
       1.09375000e-01, 2.34693289e-01, 3.11462402e-01])

In [69]:
p

array([0.   , 0.125, 0.25 , 0.375, 0.5  , 0.625, 0.75 ])

In [84]:
fig, axs = plt.subplots(6,4,figsize=(30, 30),dpi=300)
for n in group:
    tmp_df = df[df['num']==n]
    tmp_df.index = range(tmp_df.shape[0])
    lambd = sum(tmp_df['weight'])/sum(tmp_df['inten'])
    # print(lambd)
    x = np.array(tmp_df['Na'])
    lim = tmp_df.loc[0,'limit']
    com = tmp_df.loc[0,'com']
    y_real = []
    y_the = []
    for i in tmp_df.index:
        tmp_x = tmp_df.loc[i,'Na']
        tmp_real = tmp_df.loc[i,'inten']
        y_real.append(tmp_real)
    N = np.sum(y_real)*lim
    p = np.sum(tmp_df['weight'])/N

    for n_na in x:
        tmpi =binom.pmf(n_na,lim,p)
        y_the.append(tmpi)
    
    y_real =np.array(y_real)/y_real[0]*100
    y_the = np.array(y_the)/y_the[0]*100
    tmp_JS = np.round(get_JS(y_real,y_the),5)
    # plt.figure(figsize=(8,6),dpi=300)
    lw1 = 2
    lw2 = 1
    a1 = (n-1)//4
    a2 = (n-1)%4
    for i in range(len(x)):
        xx = x[i]
        y1 = y_real[i]
        y2 = y_the[i]
        axs[a1,a2].plot([xx,xx],[0,y1], lw=lw1, c='grey', zorder=1)
        axs[a1,a2].plot([xx,xx],[0,-y2], lw=lw2, c='b', zorder=2)
    sns.despine()
    axs[a1,a2].plot([min(x)-1,max(x)+1],[0,0],lw =2, c = 'k')
    axs[a1,a2].plot([0,0],[0,0],lw=lw1, c='grey',label='Exp_sp')
    axs[a1,a2].plot([0,0],[0,0],lw=lw2, c='b',label='The_sp')
    axs[a1,a2].set_title(str(com)+',lim='+str(lim)+', JS='+str(tmp_JS)+', p='+str(np.round(p,5)))
    axs[a1,a2].legend(frameon =False)
plt.tight_layout(pad=2) 
plt.show()

In [78]:
p

20.016093895517084

In [82]:
np.sum(tmp_real)*lim

2842079.82421875

In [83]:
np.sum(tmp_df['weight'])

56887336.62011719